# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model (Recurrent PPO) [10 EVs per week test]

Installing required packages and dependencies

In [1]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [2]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

Cloning into 'RL_VPP_Thesis'...
remote: Enumerating objects: 399, done.
remote: Counting objects: 100% (6/6), done.
remote: Compressing objects: 100% (6/6), done.
remote: Total 399 (delta 0), reused 2 (delta 0), pack-reused 393
Receiving objects: 100% (399/399), 151.25 MiB | 22.03 MiB/s, done.
Resolving deltas: 100% (149/149), done.
Checking out files: 100% (108/108), done.
/content/RL_VPP_Thesis
Agent_trainer_notebooks/          README.md             VPP_environment.py
data/                             Simulator_notebooks/  VPP_simulator.ipynb
Hyperparameters_sweep_notebooks/  trained_models/       wandb/


In [3]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [4]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [5]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

#case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
#case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f9b3c23d1d0>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 15
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 15, 'EVs_n_max': 783, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_energ

In [6]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [7]:
env.plot_ELVIS_data()

In [8]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  13882.37 , over-consume=kWh  32026.14 , under-consume=kWh  18143.77 , Total_cost=€  624.94 , overcost=€  1153.73 , Av.EV_en_left=kWh  100.0 , Charging_events=  783 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  83.41
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [9]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [10]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [11]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [12]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [13]:
env.plot_VPP_Elvis_comparison()

In [14]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [15]:
#env.plot_rewards_stats()

In [16]:
env.plot_EVs_kpi()

In [17]:
env.plot_actions_kpi()

In [18]:
env.plot_load_kpi()

In [19]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [20]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [21]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


## Testing dataset VPP Simulation using the loaded trained model

In [22]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  13356.2 , over-consume=kWh  31669.39 , under-consume=kWh  18313.19 , Total_cost=€  590.67 , overcost=€  1116.11 , Av.EV_en_left=kWh  100.0 , Charging_events=  783 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  83.41
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -6425.7 , over-consume=KWh  2800.34 , under-consume=KWh  9226.04 , Total_cost=€  -141.15 , Overcost=€  102.02 
 EV_INFO: Av.EV_energy_leaving=kWh  69.35 , Std.EV_energy_leaving=kWh  24.18 , EV_departures =  782 , EV_queue_left =  0
SCORE:  Cumulative_reward= 322393.1 - Step_rewars (load_t= 298782.43, EVs_energy_t= 16298.36)
 - Final_rewards (EVs_energy= 13169.28, Overconsume= -2792.83, Underconsume= -5696.11, Overcost= 2631.96)
Episode:1 Score:322393.0986489866


In [23]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [24]:
VPP_table.head(15000)

0    1    2          3              EVs_id  \
time                                                                      
2022-01-01 00:00:00   0.000000  0.0  0.0  55.121853        [0, 0, 0, 0]   
2022-01-01 00:15:00   0.000000  0.0  0.0  54.457382     [0, 0, 0, 2349]   
2022-01-01 00:30:00   0.000000  0.0  0.0  55.382381     [0, 0, 0, 2349]   
2022-01-01 00:45:00   0.000000  0.0  0.0  54.707512     [0, 0, 0, 2349]   
2022-01-01 01:00:00   0.000000  0.0  0.0  55.632511     [0, 0, 0, 2349]   
...                        ...  ...  ...        ...                 ...   
2022-06-06 04:45:00  99.989998  0.0  0.0  94.219818  [2689, 0, 0, 2690]   
2022-06-06 05:00:00  99.989998  0.0  0.0  95.260910  [2689, 0, 0, 2690]   
2022-06-06 05:15:00  99.739998  0.0  0.0  96.849457  [2689, 0, 0, 2690]   
2022-06-06 05:30:00  99.989998  0.0  0.0  97.700508  [2689, 0, 0, 2690]   
2022-06-06 05:45:00  99.989998  0.0  0.0  98.710686  [2689, 0, 0, 2690]   

                          actions                    mask_truth  \
time                                                              
2022-01-01 00:00:00  [2, 2, 2, 2]  [False, False, False, False]   
2022-01-01 00:15:00  [2, 2, 2, 1]  [False, False, False, False]   
2022-01-01 00:30:00  [2, 2, 2, 2]   [False, False, False, True]   
2022-01-01 00:45:00  [2, 2, 2, 1]  [False, False, False, False]   
2022-01-01 01:00:00  [2, 2, 2, 1]  [False, False, False, False]   
...                           ...                           ...   
2022-06-06 04:45:00  [1, 1, 2, 1]   [False, False, False, True]   
2022-06-06 05:00:00  [2, 1, 2, 1]   [False, False, False, True]   
2022-06-06 05:15:00  [1, 1, 2, 1]   [False, False, False, True]   
2022-06-06 05:30:00  [1, 1, 2, 1]   [False, False, False, True]   
2022-06-06 05:45:00  [1, 1, 2, 1]   [False, False, False, True]   

                     ev_charged_pwr  ev_discharged_pwr      load  load_reward  \
time                                                                            
2022-01-01 00:00:00        0.000000           0.000000  2.446357    15.000000   
2022-01-01 00:15:00        0.000000          -2.657890  0.000000    -8.374437   
2022-01-01 00:30:00        3.700000           0.000000  6.087068    15.000000   
2022-01-01 00:45:00        0.000000          -2.699472  0.000000    -7.445490   
2022-01-01 01:00:00        3.700000           0.000000  5.374876    -6.277079   
...                             ...                ...       ...          ...   
2022-06-06 04:45:00        2.565619           0.000000 -5.131213    -8.935206   
2022-06-06 05:00:00        4.164376           0.000000 -8.328726    -7.140163   
2022-06-06 05:15:00        6.354180          -1.000000 -6.354180    -6.643984   
2022-06-06 05:30:00        4.404204           0.000000 -5.808383    -8.710375   
2022-06-06 05:45:00        4.040719           0.000000 -8.081412    -8.561844   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  15.000000  
2022-01-01 00:15:00        0.0  -8.374437  
2022-01-01 00:30:00        0.0  15.000000  
2022-01-01 00:45:00        0.0  -7.445490  
2022-01-01 01:00:00        0.0  -6.277079  
...                        ...        ...  
2022-06-06 04:45:00        0.0  -8.935206  
2022-06-06 05:00:00        0.0  -7.140163  
2022-06-06 05:15:00        0.0  -6.643984  
2022-06-06 05:30:00        0.0  -8.710375  
2022-06-06 05:45:00        0.0  -8.561844  

[15000 rows x 13 columns]

In [25]:
#env.plot_Elvis_results()

In [26]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [27]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [28]:
env.plot_VPP_Elvis_comparison()

In [29]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [30]:
env.plot_rewards_stats()

In [31]:
env.plot_EVs_kpi()

In [32]:
env.plot_load_kpi()

In [33]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [34]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 3133, Arrival time: 2022-01-01 01:15:00, Parking_time: 24, Leaving_time: 2022-01-02 01:15:00, SOC: 0.5854415752317004, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 3915, Arrival time: 2022-12-31 15:15:00, Parking_time: 24, Leaving_time: 2023-01-01 15:15:00, SOC: 0.4108008725830445, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  5091.99 , over-consume=kWh  28311.18 , under-consume=kWh  23219.19 , Total_cost=€  311.82 , overcost=€  1250.28 , Charging_events=  783 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  91.15


In [35]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [36]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [37]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  4503.88 , over-consume=kWh  27992.93 , under-consume=kWh  23489.04 , Total_cost=€  287.39 , overcost=€  1240.5 , Av.EV_en_left=kWh  100.0 , Charging_events=  783 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  91.15
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -10383.13 , over-consume=KWh  1905.2 , under-consume=KWh  12288.33 , Total_cost=€  -392.12 , Overcost=€  86.08 
 EV_INFO: Av.EV_energy_leaving=kWh  74.81 , Std.EV_energy_leaving=kWh  22.29 , EV_departures =  782 , EV_queue_left =  0
SCORE:  Cumulative_reward= 319066.45 - Step_rewars (load_t= 276252.5, EVs_energy_t= 29903.14)
 - Final_rewards (EVs_energy= 14116.42, Overconsume= -1961.64, Underconsume= -6059.1, Overcost= 6815.13)
Episode:1 Score:319066.449769386


In [38]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [39]:
VPP_table.head(15000)

0    1    2    3           EVs_id       actions  \
time                                                                           
2022-01-01 00:00:00   0.000000  0.0  0.0  0.0     [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00   0.000000  0.0  0.0  0.0     [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00   0.000000  0.0  0.0  0.0     [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00   0.000000  0.0  0.0  0.0     [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00   0.000000  0.0  0.0  0.0     [0, 0, 0, 0]  [2, 0, 1, 0]   
...                        ...  ...  ...  ...              ...           ...   
2022-06-06 04:45:00  98.288315  0.0  0.0  0.0  [5043, 0, 0, 0]  [1, 0, 0, 0]   
2022-06-06 05:00:00  99.989998  0.0  0.0  0.0  [5043, 0, 0, 0]  [1, 0, 0, 0]   
2022-06-06 05:15:00  99.989998  0.0  0.0  0.0  [5043, 0, 0, 0]  [1, 0, 0, 0]   
2022-06-06 05:30:00  99.989998  0.0  0.0  0.0  [5043, 0, 0, 0]  [1, 0, 0, 0]   
2022-06-06 05:45:00  99.989998  0.0  0.0  0.0  [5043, 0, 0, 0]  [1, 0, 0, 0]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00  [False, False, False, True]        0.000000   
2022-01-01 00:45:00  [False, False, False, True]        0.000000   
2022-01-01 01:00:00   [False, True, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 04:45:00     [True, True, True, True]       10.440078   
2022-06-06 05:00:00     [True, True, True, True]        6.806741   
2022-06-06 05:15:00     [True, True, True, True]        0.000009   
2022-06-06 05:30:00     [True, True, True, True]        0.000009   
2022-06-06 05:45:00     [True, True, True, True]        0.000009   

                     ev_discharged_pwr       load  load_reward  EV_reward  \
time                                                                        
2022-01-01 00:00:00                0.0  -4.442504    -3.074076        0.0   
2022-01-01 00:15:00                0.0  -2.844446    -4.518473        0.0   
2022-01-01 00:30:00                0.0  -3.711084    -2.537897        0.0   
2022-01-01 00:45:00                0.0  -2.522738    -5.483765        0.0   
2022-01-01 01:00:00                0.0  -4.532142    -5.240734        0.0   
...                                ...        ...          ...        ...   
2022-06-06 04:45:00                0.0   0.000000    -8.057992        0.0   
2022-06-06 05:00:00                0.0  -7.363791   -15.289953        0.0   
2022-06-06 05:15:00                0.0 -15.289953   -13.529029        0.0   
2022-06-06 05:30:00                0.0 -13.381932   -13.596832        0.0   
2022-06-06 05:45:00                0.0 -13.456515   -14.217714        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -3.074076  
2022-01-01 00:15:00  -4.518473  
2022-01-01 00:30:00  -2.537897  
2022-01-01 00:45:00  -5.483765  
2022-01-01 01:00:00  -5.240734  
...                        ...  
2022-06-06 04:45:00  -8.057992  
2022-06-06 05:00:00 -15.289953  
2022-06-06 05:15:00 -13.529029  
2022-06-06 05:30:00 -13.596832  
2022-06-06 05:45:00 -14.217714  

[15000 rows x 13 columns]

In [40]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [41]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [42]:
env.plot_VPP_Elvis_comparison()

In [43]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [44]:
env.plot_rewards_stats()

In [45]:
env.plot_EVs_kpi()

In [46]:
env.plot_load_kpi()

In [47]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [48]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 5482, Arrival time: 2022-01-01 12:30:00, Parking_time: 22.636500354825355, Leaving_time: 2022-01-02 11:08:11.401277, SOC: 0.5388265685289098, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 6264, Arrival time: 2022-12-29 17:30:00, Parking_time: 22.67528806656917, Leaving_time: 2022-12-30 16:10:31.037040, SOC: 0.6895892109765083, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  515.14 , over-consume=kWh  25871.18 , under-consume=kWh  25356.04 , Total_cost=€  127.79 , overcost=€  1063.61 , Charging_events=  783 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  95.56


In [49]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [50]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [51]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  1131.21 , over-consume=kWh  26686.76 , under-consume=kWh  25555.55 , Total_cost=€  201.64 , overcost=€  1128.82 , Av.EV_en_left=kWh  100.0 , Charging_events=  783 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  95.56
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -12444.27 , over-consume=KWh  1676.04 , under-consume=KWh  14120.32 , Total_cost=€  -416.95 , Overcost=€  68.46 
 EV_INFO: Av.EV_energy_leaving=kWh  77.45 , Std.EV_energy_leaving=kWh  21.66 , EV_departures =  781 , EV_queue_left =  0
SCORE:  Cumulative_reward= 311554.92 - Step_rewars (load_t= 262301.35, EVs_energy_t= 35032.09)
 - Final_rewards (EVs_energy= 14100.8, Overconsume= -1747.11, Underconsume= -6610.02, Overcost= 8477.81)
Episode:1 Score:311554.9182301506


In [52]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [53]:
VPP_table.head(14995)

0    1    2    3        EVs_id       actions  \
time                                                                  
2022-01-01 00:00:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 0, 1, 0]   
...                  ...  ...  ...  ...           ...           ...   
2022-06-06 03:30:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 0, 1, 0]   
2022-06-06 03:45:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 0, 1, 0]   
2022-06-06 04:00:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 0, 1, 0]   
2022-06-06 04:15:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 0, 1, 0]   
2022-06-06 04:30:00  0.0  0.0  0.0  0.0  [0, 0, 0, 0]  [2, 2, 1, 2]   

                                       mask_truth  ev_charged_pwr  \
time                                                                
2022-01-01 00:00:00   [False, False, False, True]             0.0   
2022-01-01 00:15:00   [False, False, False, True]             0.0   
2022-01-01 00:30:00   [False, False, False, True]             0.0   
2022-01-01 00:45:00   [False, False, False, True]             0.0   
2022-01-01 01:00:00    [False, True, False, True]             0.0   
...                                           ...             ...   
2022-06-06 03:30:00    [False, True, False, True]             0.0   
2022-06-06 03:45:00    [False, True, False, True]             0.0   
2022-06-06 04:00:00    [False, True, False, True]             0.0   
2022-06-06 04:15:00    [False, True, False, True]             0.0   
2022-06-06 04:30:00  [False, False, False, False]             0.0   

                     ev_discharged_pwr      load  load_reward  EV_reward  \
time                                                                       
2022-01-01 00:00:00                0.0 -3.078186    -5.291383        0.0   
2022-01-01 00:15:00                0.0 -4.320521    -5.337742        0.0   
2022-01-01 00:30:00                0.0 -4.371516    -5.040332        0.0   
2022-01-01 00:45:00                0.0 -4.044366    -5.883557        0.0   
2022-01-01 01:00:00                0.0 -4.971912    -6.274737        0.0   
...                                ...       ...          ...        ...   
2022-06-06 03:30:00                0.0 -3.259047    -5.624977        0.0   
2022-06-06 03:45:00                0.0 -4.687475    -7.701489        0.0   
2022-06-06 04:00:00                0.0 -6.971638    -6.956676        0.0   
2022-06-06 04:15:00                0.0 -6.152343    -7.801739        0.0   
2022-06-06 04:30:00                0.0 -7.081913    -7.209341        0.0   

                      rewards  
time                           
2022-01-01 00:00:00 -5.291383  
2022-01-01 00:15:00 -5.337742  
2022-01-01 00:30:00 -5.040332  
2022-01-01 00:45:00 -5.883557  
2022-01-01 01:00:00 -6.274737  
...                       ...  
2022-06-06 03:30:00 -5.624977  
2022-06-06 03:45:00 -7.701489  
2022-06-06 04:00:00 -6.956676  
2022-06-06 04:15:00 -7.801739  
2022-06-06 04:30:00 -7.209341  

[14995 rows x 13 columns]

In [54]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [55]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [56]:
env.plot_VPP_Elvis_comparison()

In [57]:
env.plot_rewards_results()

In [58]:
env.plot_rewards_stats()

In [59]:
env.plot_EVs_kpi()

In [60]:
env.plot_actions_kpi()

In [61]:
env.plot_load_kpi()

In [62]:
env.plot_yearly_load_log()

In [63]:
#env.close()